In [1]:
import pandas as pd

def readCSV():
    df = pd.read_csv('./jira_data.csv') 
    
    return df


In [2]:
df = readCSV()

### Issues count per project ###

| project_id | project_key | project_name | task_count | epic_count
| --- | --- | --- | --- | --- |
| 109| EXLUEILWITZ| Rerum sequi non et.| 47| 6| 
| 286| REICIENDISMACGYVER| Dolorem alias quis at perferendis.| 81| 2| 
| 292| VELITONDRICKA| Modi facilis iste vel at aut.| 27| 3| 
| 455| ETLANG| Consequatur unde optio autem.| 165| 28| 
| 459| QUAEWATSICA| Provident animi atque facere minus.| 621| 12| 
| 581| MOLLITIAWEHNER| Ut incidunt aliquid maxime voluptas eveniet laborum adipisci doloribus.| 78| 7| 
| 616| OPTIOHERMANN-RUTHERFORD| Quia voluptatem in et.| 179| 15| 
| 652| FACILISJAKUBOWSKI| Sit fuga et voluptatem fugiat reprehenderit quis enim omnis.| 72| 6| 
| 688| ODIODURGAN-BOEHM| Eius nam omnis aut dolorem.| 156| 15| 
| 798| ODIORUECKER-WATSICA| Aut autem nisi aut eaque et odio.| 22| 5| 
| 818| CORPORISVEUM-HEATHCOTE| Esse pariatur fugiat enim est.| 63| 10| 
| 840| NISIRUTHERFORD-TROMP| Explicabo aut expedita quod cupiditate quo sed maiores.| 271| 14| 
| 938| FACILISLUBOWITZ| Quaerat porro nihil vel.| 6| 1| 
| 950| CONSEQUATURCASSIN-GLOVER| Amet earum delectus quo.| 136| 8| 



### Encode the data for classification performance

In [3]:
from io import StringIO

col = ['issue', 'epic', 'summary', 'clean_summary', 'epic_clean_summary', 'project_key']
df_encode = df[col]
df_encode = df_encode[pd.notnull(df_encode['summary'])]
df_encode.columns = ['issue', 'epic', 'summary', 'clean_summary', 'epic_clean_summary', 'project_key']
df['category_id'] = df['epic'].factorize()[0]
df_encode['category_id'] = df['category_id']
category_id_df = df[['epic', 'category_id']].drop_duplicates().sort_values('category_id')
category_to_id = dict(category_id_df.values)
id_to_category = dict(category_id_df[['category_id', 'epic']].values)
df_encode['clean_summary'] = df_encode['clean_summary'].str.replace('|',' ')
df_encode['epic_clean_summary'] = df_encode['epic_clean_summary'].str.replace('|',' ')
# df['range'] = df['range'].str.replace(',','-')
df_encode

issue                         epic  \
0                   QUAEWATSICA-11               QUAEWATSICA-10   
1                   QUAEWATSICA-12               QUAEWATSICA-10   
2                   QUAEWATSICA-13               QUAEWATSICA-10   
3                   QUAEWATSICA-14               QUAEWATSICA-10   
4                   QUAEWATSICA-15               QUAEWATSICA-10   
...                            ...                          ...   
1919  CONSEQUATURCASSIN-GLOVER-182  CONSEQUATURCASSIN-GLOVER-15   
1920      NISIRUTHERFORD-TROMP-320       NISIRUTHERFORD-TROMP-8   
1921  CONSEQUATURCASSIN-GLOVER-183  CONSEQUATURCASSIN-GLOVER-15   
1922  CONSEQUATURCASSIN-GLOVER-184  CONSEQUATURCASSIN-GLOVER-15   
1923  CONSEQUATURCASSIN-GLOVER-190  CONSEQUATURCASSIN-GLOVER-15   

                                                summary  \
0                     Persist user tokens into database   
1                              Fetch user activity data   
2     Synchronize activity data with information in ...   
3             Implement fitbit activity data subscriber   
4       Synchronize logged activities on Fitbit by User   
...                                                 ...   
1919                               Create user redesign   
1920                                      Release 1.0.3   
1921                                        Pisca pisca   
1922                                 Fix UI on empty DB   
1923                         Offline access improvement   

                                      clean_summary  \
0                       persist user token database   
1                         fetch user activity datum   
2     synchronize activity datum information fitbit   
3        implement fitbit activity datum subscriber   
4              synchronize log activity fitbit user   
...                                             ...   
1919                           create user redesign   
1920                                        release   
1921                                    pisca pisca   
1922                                      fix ui db   
1923                     offline access improvement   

                                     epic_clean_summary  \
0                     integrate fitbit account souschef   
1                     integrate fitbit account souschef   
2                     integrate fitbit account souschef   
3                     integrate fitbit account souschef   
4                     integrate fitbit account souschef   
...                                                 ...   
1919                                         mobileware   
1920  t2.5 android u0026 ios app delevopment improve...   
1921                                         mobileware   
1922                                         mobileware   
1923                                         mobileware   

                   project_key  category_id  
0                  QUAEWATSICA            0  
1                  QUAEWATSICA            0  
2                  QUAEWATSICA            0  
3                  QUAEWATSICA            0  
4                  QUAEWATSICA            0  
...                        ...          ...  
1919  CONSEQUATURCASSIN-GLOVER          119  
1920      NISIRUTHERFORD-TROMP          104  
1921  CONSEQUATURCASSIN-GLOVER          119  
1922  CONSEQUATURCASSIN-GLOVER          119  
1923  CONSEQUATURCASSIN-GLOVER          119  

[1924 rows x 7 columns]

### Get the count of the word in the text document using "CountVectorizer"

In [4]:
from sklearn.feature_extraction.text import CountVectorizer

def get_count_vectorizer_matrix(proj_train):
    count_vect = CountVectorizer(binary=True)
    X_train_counts = count_vect.fit_transform(proj_train)
    return X_train_counts, count_vect

### Apply TF-IDF method to create document frequency score

In [5]:
from sklearn.feature_extraction.text import TfidfTransformer

def get_tfidf_matrix(X_train_counts):
    tfidf_transformer = TfidfTransformer()
    X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)
    
#     print(X_train_tfidf)
    return X_train_tfidf


### Predict the categories based on the transformed text vectors

In [6]:
#docs_new = ['receive|message ', 'hour|message|wrong', 'offline|access|improvement', 'improvement', '']
from sklearn.feature_extraction.text import TfidfTransformer

def predict(model, count_vect, X_train_tfidf, y_train, X_test):
    clf = model.fit(X_train_tfidf, y_train)
    docs_new = X_test
    tfidf_transformer = TfidfTransformer()
    X_new_counts = count_vect.transform(docs_new)
    X_new_tfidf = tfidf_transformer.fit_transform(X_new_counts)

    predicted = clf.predict(X_new_tfidf)
#     print('-----PREDICTION-----')
#     for doc, category in zip(docs_new, predicted):
#        print('%r => %s' % (doc, category))

    return predicted


### (Approach): Apply cross validation using 6-fold split for tasks within a project

In [9]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import KFold
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from numpy import mean
from numpy import std
from sklearn.pipeline import Pipeline
import numpy as np

def get_cross_val_task(df, proj, model):
    # get the train and test dataset for the projects

    project_data = df.loc[df['project_key'] == proj]
    model_scores = []
    
    print('project_data.shape::', project_data.shape)

    X = project_data['clean_summary'].values.astype('U')
    y = project_data['epic']
    
    X = np.array(X)
    y = np.array(y)
    kf = KFold(n_splits=6, shuffle=True, random_state=1)
#     kf = StratifiedKFold(n_splits=6)
#     print('number of splitting iterations::', kf.get_n_splits(X, y))

    accuracy_scores = []
    weighted_accuracy_scores = []
    f1_scores = []
    precision_scores = []
    recall_scores = []
#     roc_auc_scores = []
    for train_index, test_index in kf.split(X, y):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        count_vectorizer_output = get_count_vectorizer_matrix(X_train)
        X_train_counts = count_vectorizer_output[0]
        count_vect = count_vectorizer_output[1]
    
        # tfidf matrix
        X_train_tfidf = get_tfidf_matrix(X_train_counts)

        predicted = predict(model, count_vect, X_train_tfidf, y_train, X_test)
#         print('total instances:', len(X))
#         print('no of instances used:', len(X_test))
#         print('accuaracy of a model:', accuracy_score(y_test, predicted))
        weighted_score = (len(X_test) / len(X)) * accuracy_score(y_test, predicted)
#         print('weighted_score accuracy of a model:', weighted_score)
        
        accuracy_scores.append(accuracy_score(y_test, predicted))
        weighted_accuracy_scores.append(weighted_score)
        f1_scores.append(f1_score(y_test, predicted, average='weighted'))
        precision_scores.append(precision_score(y_test, predicted, average='weighted'))
        recall_scores.append(recall_score(y_test, predicted, average='weighted'))
#         roc_auc_scores.append(roc_auc_score(y_test, predicted, average='weighted'))
        
    print('accuracy for 6-splits:', accuracy_scores)
    print('f1_scores for 6-splits:', f1_scores)
    print('precision_scores for 6-splits:', precision_scores)
    print('recall_scores for 6-splits:', recall_scores)
    print('weighted_accuracy_scores for 6-splits:', weighted_accuracy_scores)
#     print('roc_auc_scores for 6-splits:', roc_auc_scores)
    
    return accuracy_scores, f1_scores, precision_scores, recall_scores, np.array(weighted_accuracy_scores).sum()


In [10]:
from sklearn.linear_model import SGDClassifier #SVM: SGDClassifier()
from sklearn.naive_bayes import MultinomialNB #MultinomialNB:: MultinomialNB()
from sklearn.ensemble import RandomForestClassifier #RandomForest:: RandomForestClassifier(n_estimators=1000, max_depth=3, random_state=0)
from sklearn.svm import LinearSVC #SVM: LinearSVC()
from xgboost import XGBClassifier #XGBoost: XGBClassifier()
import pandas as pd

project_list = [
    'QUAEWATSICA', 
    'ETLANG', 
    'VELITONDRICKA', 
    'MOLLITIAWEHNER', 
    'EXLUEILWITZ', 
    'ODIODURGAN-BOEHM', 
    'REICIENDISMACGYVER', 
    'OPTIOHERMANN-RUTHERFORD', 
    'ODIORUECKER-WATSICA', 
    'NISIRUTHERFORD-TROMP', 
    'CORPORISVEUM-HEATHCOTE', 
    'CONSEQUATURCASSIN-GLOVER',
#     'FACILISLUBOWITZ',
#     'FACILISJAKUBOWSKI', 
]


accuracy_scores = []
f1_scores = []
precision_scores = []
recall_scores = []
weighted_accuracy_scores = []
results = []

model_accuracy_scores = []
model_f1_scores = []
model_precision_scores = []
model_recall_scores = []
model_weighted_accuracy_scores = []

model = {
    1: MultinomialNB(), 
    2: RandomForestClassifier(n_estimators=1000, max_depth=3, random_state=0),
    3: LinearSVC(),
    4: SGDClassifier(),
    5: XGBClassifier(num_class=6)
}

for key in [1, 2, 3, 4, 5]:
    print('model: %s' % model[key])
    for proj in project_list:
        print('project: %s' % proj)
        scores = get_cross_val_task(df_encode, proj, model[key])
        print('')
        accuracy_scores.append(np.array(scores[0]).mean())
        f1_scores.append(np.array(scores[1]).mean())
        precision_scores.append(np.array(scores[2]).mean())
        recall_scores.append(np.array(scores[3]).mean())
        weighted_accuracy_scores.append(np.array(scores[4]).mean())
    print('mean model accuracy score for %s => %s' % (proj, accuracy_scores))
    print('mean model f1 score for %s => %s' % (proj, f1_scores))
    print('mean model precision score for %s => %s' % (proj, precision_scores))
    print('mean model recall score for %s => %s' % (proj, recall_scores))
    print('mean model weighted accuracy score for %s => %s' % (proj, weighted_accuracy_scores))
    
    model_accuracy_scores.append(np.array(accuracy_scores).mean())
    model_f1_scores.append(np.array(f1_scores).mean())
    model_precision_scores.append(np.array(precision_scores).mean())
    model_recall_scores.append(np.array(recall_scores).mean())
    model_weighted_accuracy_scores.append(np.array(weighted_accuracy_scores).mean())
    
    accuracy_scores = []
    f1_scores = []
    precision_scores = []
    recall_scores = []
    weighted_accuracy_scores = []
    
result_data = {
    'Accuracy':model_accuracy_scores,
    'F1-Score':model_f1_scores,
    'Precision':model_precision_scores,
    'Recall':model_recall_scores,
    'Weighted accuracy':model_weighted_accuracy_scores
}
# 
results = pd.DataFrame(result_data, index = ['Multinomial NB', 'Random Forest', 'LinearSVC', 'SGDClassifier', 'XGBoost'])
# results = pd.DataFrame(result_data, index = ['XGBoost'])
print('results:', results)    
# print('list of model scores:', model_scores)
# print('average model accuracy score', np.array(accuracy_scores).mean())
# print('average model f1 score', np.array(f1_scores).mean())
# print('average model precision score', np.array(precision_scores).mean())
# print('average model recall score', np.array(recall_scores).mean())
# print('average model weighted accuracy score', np.array(weighted_accuracy_scores).mean())


model: MultinomialNB()
project: QUAEWATSICA
project_data.shape:: (621, 7)


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedM

accuracy for 6-splits: [0.47115384615384615, 0.5, 0.5, 0.44660194174757284, 0.4174757281553398, 0.4077669902912621]
f1_scores for 6-splits: [0.3987293751999634, 0.42833021282897515, 0.42789139528490444, 0.37422811160675246, 0.3367251680358476, 0.3382119841284234]
precision_scores for 6-splits: [0.44815070373511523, 0.4389042534945545, 0.46340446083596765, 0.4053010001610801, 0.32911554464952525, 0.36254192409532215]
recall_scores for 6-splits: [0.47115384615384615, 0.5, 0.5, 0.44660194174757284, 0.4174757281553398, 0.4077669902912621]
weighted_accuracy_scores for 6-splits: [0.0789049919484702, 0.08373590982286634, 0.08373590982286634, 0.07407407407407407, 0.06924315619967793, 0.06763285024154589]

project: ETLANG
project_data.shape:: (165, 7)


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:670: UserWarning:

accuracy for 6-splits: [0.32142857142857145, 0.25, 0.2857142857142857, 0.2962962962962963, 0.2962962962962963, 0.25925925925925924]
f1_scores for 6-splits: [0.20794930875576037, 0.12321428571428572, 0.1660714285714286, 0.1580246913580247, 0.18271604938271604, 0.12305854241338111]
precision_scores for 6-splits: [0.22999999999999998, 0.10302197802197802, 0.15659340659340662, 0.11594202898550725, 0.18518518518518517, 0.09037037037037036]
recall_scores for 6-splits: [0.32142857142857145, 0.25, 0.2857142857142857, 0.2962962962962963, 0.2962962962962963, 0.25925925925925924]
weighted_accuracy_scores for 6-splits: [0.05454545454545455, 0.04242424242424243, 0.048484848484848485, 0.048484848484848485, 0.048484848484848485, 0.04242424242424242]

project: VELITONDRICKA
project_data.shape:: (27, 7)
accuracy for 6-splits: [0.6, 0.6, 0.6, 1.0, 1.0, 1.0]
f1_scores for 6-splits: [0.52, 0.5333333333333333, 0.5333333333333333, 1.0, 1.0, 1.0]
precision_scores for 6-splits: [0.4666666666666666, 0.6, 0.6, 

...

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[06:56:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[06:56:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
accuracy for 6-splits: [0.7391304347826086, 0.7391304347826086, 0.7391304347826086, 0.782608695652174, 0.7727272727272727, 0.8181818181818182]
f1_scores for 6-splits: [0.6282608695652173, 0.6282608695652173, 0.7170099160945843, 0.7048054919908466, 0.7511019283746556, 0.7595693779904306]
precision_scores for 6-splits: [0.5463137996219282, 0.5463137996219282, 0.7130434782608696, 0.6418219461697723, 0.7518939393939393, 0.761904761904762]
recall_scores for 6-splits: [0.7391304347826086, 0.7391304347826086, 0.7391304347826086, 0.782608695652174, 0.7727272727272727, 0.8181818181818182]
weighted_accuracy_scores for 6-splits: [0.125, 0.125, 0.125, 0.1323529411764706, 0.125, 0.132352941176

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


### (Approach 5): Apply Optuna hyper parameter tuning

In [47]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import KFold
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from numpy import mean
from numpy import std
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC

def get_cross_val_task_optuna(trial):
    project_list = [
        'QUAEWATSICA', 
        'ETLANG', 
        'VELITONDRICKA', 
        'MOLLITIAWEHNER', 
        'EXLUEILWITZ', 
        'ODIODURGAN-BOEHM', 
        'REICIENDISMACGYVER', 
        'OPTIOHERMANN-RUTHERFORD', 
        'ODIORUECKER-WATSICA', 
        'NISIRUTHERFORD-TROMP', 
        'CORPORISVEUM-HEATHCOTE', 
        'CONSEQUATURCASSIN-GLOVER',
#         'FACILISLUBOWITZ',
#         'FACILISJAKUBOWSKI', 
    ]
    
    accuracy_scores = []
    f1_scores = []
    
    for proj in project_list:
        f1_scores_split = []
        print('project: %s' % proj)
        df = df_encode
        project_data = df.loc[df['project_key'] == proj]

        print('project_data.shape::', project_data.shape)

        X = project_data['clean_summary']
        y = project_data['epic']

        X = np.array(X)
        y = np.array(y)
        kf = KFold(n_splits=6, shuffle=True, random_state=1)

# #         Model 1: Random Forest        
#         n_estimators = trial.suggest_int('n_estimators', 2, 20)
#         max_depth = int(trial.suggest_loguniform('max_depth', 1, 32))
#         model = RandomForestClassifier(n_estimators=n_estimators, max_depth=max_depth)


# #         Model 2: LinearSVC
#         model = SVC(kernel='linear', gamma="auto")

# #         Model 3: XGBoost
        param = {
                    "n_estimators" : trial.suggest_int('n_estimators', 0, 1000),
                    'max_depth':trial.suggest_int('max_depth', 2, 25),
                    'reg_alpha':trial.suggest_int('reg_alpha', 0, 5),
                    'reg_lambda':trial.suggest_int('reg_lambda', 0, 5),
                    'min_child_weight':trial.suggest_int('min_child_weight', 0, 5),
                    'gamma':trial.suggest_int('gamma', 0, 5),
                    'learning_rate':trial.suggest_loguniform('learning_rate',0.005,0.5),
                    'colsample_bytree':trial.suggest_discrete_uniform('colsample_bytree',0.1,1,0.01),
                    'nthread' : -1
                }
        model = XGBClassifier(**param)


# #         Model 4: SVC
#          svc_c = trial.suggest_loguniform('svc_c', 1e-10, 1e10)
#          model = sklearn.svm.SVC(C=svc_c, gamma='auto')

        
        for train_index, test_index in kf.split(X, y):
            X_train, X_test = X[train_index], X[test_index]
            y_train, y_test = y[train_index], y[test_index]
            count_vectorizer_output = get_count_vectorizer_matrix(X_train)
            X_train_counts = count_vectorizer_output[0]
            count_vect = count_vectorizer_output[1]

            # tfidf matrix
            X_train_tfidf = get_tfidf_matrix(X_train_counts)

            predicted = predict(model, count_vect, X_train_tfidf, y_train, X_test)
            f1_scores_split.append(f1_score(y_test, predicted, average='weighted'))
    
        f1_scores.append(np.array(f1_scores_split).mean())

    print('f1_scores:', np.array(f1_scores).mean())
    return np.array(f1_scores).mean()

### Get an optimal f1-score with 100 trials

In [48]:
from sklearn.linear_model import SGDClassifier #SVM: SGDClassifier()
from sklearn.naive_bayes import MultinomialNB #MultinomialNB:: MultinomialNB()
from sklearn.ensemble import RandomForestClassifier #RandomForest:: RandomForestClassifier(n_estimators=1000, max_depth=3, random_state=0)
from sklearn.svm import LinearSVC #SVM: LinearSVC()
from xgboost import XGBClassifier #XGBoost: XGBClassifier()
import optuna

study = optuna.create_study(direction='maximize')
study.optimize(get_cross_val_task_optuna, n_trials=100)

trial = study.best_trial

print('F1 Score: {}'.format(trial.value))


[I 2021-05-26 13:16:48,136] A new study created in memory with name: no-name-53bed45d-5617-4d6e-95fc-af9608357daa
C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


project: QUAEWATSICA
project_data.shape:: (621, 7)
[13:16:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[13:16:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


...

[19:00:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\lib\site-packages\xgboost\sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[19:00:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


[I 2021-05-26 19:00:30,118] Trial 99 finished with value: 0.3480685389875591 and parameters: {'n_estimators': 643, 'max_depth': 22, 'reg_alpha': 0, 'reg_lambda': 2, 'min_child_weight': 4, 'gamma': 0, 'learning_rate': 0.032516760757620125, 'colsample_bytree': 0.86}. Best is trial 97 with value: 0.5618991864631359.


f1_scores: 0.3480685389875591
F1 Score: 0.5618991864631359


### Results of the models: ###

### Metrics used Accuracy, F1-score, Precision, Recall, Weighted Average

| --- | Random forest |Multinomial Naive Bayes|SGDClassifier|LinearSVC|XGBoost
| --- | --- | --- | --- | --- | --- |
| Accuracy| 50.46746988| 55.80569899| 61.08376065| 62.07692338| 56.64141844
| F1-Score| 40.82062274| 48.73799776| 60.29856176| 57.50378251| 52.16391074
| Precision| 39.25255127| 48.89874888| 63.55695146| 58.65400480| 53.1796943
| Recall| 50.46746988| 55.80569899| 61.08376065| 62.07692338| 56.64141844
| Weighted accuracy| 50.52285601| 55.82911205| 61.69389651| 62.19266598| 56.76536158

### F1 Scores optimized with optuna

Random Forest: 
Trial 99 finished with value: 0.5422728892031464 and parameters: {'n_estimators': 17, 'max_depth': 18.694494544210215}. Best is trial 71 with value: 0.56837380556999.

SVC:
Trial 99 finished with value: 60.29856176 and parameters: {'n_estimators': 17, 'max_depth': 18.694494544210215}. Best is trial 0 with value: 0.6029856176.

LinearSVC:
Trial 99 finished with value: 0.5750378251934886 and parameters: {'n_estimators': 9, 'max_depth': 1.8792925549037873}. Best is trial 0 with value: 0.5750378251934886.

XGBoost:
Trial 99 finished with value: 0.3480685389875591 and parameters: {'n_estimators': 643, 'max_depth': 22, 'reg_alpha': 0, 'reg_lambda': 2, 'min_child_weight': 4, 'gamma': 0, 'learning_rate': 0.032516760757620125, 'colsample_bytree': 0.86}. Best is trial 97 with value: 0.5618991864631359.